In [1]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor

In [4]:
# 🔹 Load the Datasets
import pandas as pd

train = pd.read_csv("train_simp_fixedOrdinal_FE_noscale(15k).csv")
test = pd.read_csv("test_simp_fixedOrdinal_FE_noscale(15k).csv")
sample_submission = pd.read_csv("home-data-for-ml-course/sample_submission.csv")

# 🔹 Define Features (X) and Target (y)
y_train = train["SalePrice"]
X_train = train.drop(columns=["SalePrice"])
X_test = test.copy()


In [ ]:
# from sklearn.linear_model import Lasso
# from sklearn.model_selection import GridSearchCV

# # 🔹 Define Hyperparameter Grid
# param_grid = {"alpha": [0.0001, 0.001, 0.01, 0.1, 1, 10]}

# # 🔹 Grid Search with Cross-Validation
# grid_search = GridSearchCV(Lasso(), param_grid, cv=5, scoring="r2", n_jobs=-1)
# grid_search.fit(X_train, y_train)

# # 🔹 Best Model
# best_lasso = grid_search.best_estimator_
# print("✅ Best Lasso Alpha:", grid_search.best_params_)

# # 🔹 Predict & Save
# y_test_pred = best_lasso.predict(X_test)
# submission = pd.DataFrame({"Id": test["Id"], "SalePrice": y_test_pred})
# submission.to_csv("Lasso_Optimized.csv", index=False)
# print("✅ Lasso predictions saved!")



✅ Best Lasso Alpha: {'alpha': 10}
✅ Lasso predictions saved!


c:\Users\dhiaa\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\linear_model\_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 3.279e+11, tolerance: 9.053e+08
  model = cd_fast.enet_coordinate_descent(


In [ ]:
import optuna
from xgboost import XGBRegressor
from sklearn.model_selection import cross_val_score

# 🔹 Define Objective Function
def objective(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 100, 1000, step=50),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.2),
        "max_depth": trial.suggest_int("max_depth", 3, 15),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "random_state": 42
    }
    model = XGBRegressor(**params)
    score = cross_val_score(model, X_train, y_train, cv=5, scoring="r2").mean()
    return score

# 🔹 Run Optimization
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

# 🔹 Train Best Model
best_xgb = XGBRegressor(**study.best_params)
best_xgb.fit(X_train, y_train)
print("✅ Best XGBoost Parameters:", study.best_params)

# 🔹 Predict & Save
y_test_pred = best_xgb.predict(X_test)
submission = pd.DataFrame({"Id": test["Id"], "SalePrice": y_test_pred})
submission.to_csv("XGBoost_Optimized.csv", index=False)
print("✅ XGBoost predictions saved!")

c:\Users\dhiaa\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[I 2025-03-09 11:35:09,915] A new study created in memory with name: no-name-e1640cc2-e1b8-42b0-a6bd-7c05bc61b132
[I 2025-03-09 11:35:13,178] Trial 0 finished with value: 0.9152815461158752 and parameters: {'n_estimators': 150, 'learning_rate': 0.09775871165049096, 'max_depth': 7, 'subsample': 0.6381900911917596, 'colsample_bytree': 0.7301056591601661}. Best is trial 0 with value: 0.9152815461158752.
[I 2025-03-09 11:35:27,177] Trial 1 finished with value: 0.9069242000579834 and parameters: {'n_estimators': 850, 'learning_rate': 0.14410972786261644, 'max_depth': 7, 'subsample': 0.8830567260082032, 'colsample_bytree': 0.7404166853970777}. Best is trial 0 with value: 0.9152815461158752.
[I 2025-03-09 11:35:32,491] 

✅ Best XGBoost Parameters: {'n_estimators': 1000, 'learning_rate': 0.016864808928665143, 'max_depth': 3, 'subsample': 0.687663887517002, 'colsample_bytree': 0.9790871051696873}
✅ XGBoost predictions saved!


In [ ]:
# from lightgbm import LGBMRegressor

# # 🔹 Define Objective Function
# def objective(trial):
#     params = {
#         "n_estimators": trial.suggest_int("n_estimators", 100, 1000, step=50),
#         "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.2),
#         "max_depth": trial.suggest_int("max_depth", 3, 15),
#         "num_leaves": trial.suggest_int("num_leaves", 20, 300),
#         "subsample": trial.suggest_float("subsample", 0.6, 1.0),
#         "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
#         "random_state": 42
#     }
#     model = LGBMRegressor(**params)
#     score = cross_val_score(model, X_train, y_train, cv=5, scoring="r2").mean()
#     return score

# # 🔹 Run Optimization
# study = optuna.create_study(direction="maximize")
# study.optimize(objective, n_trials=50)

# # 🔹 Train Best Model
# best_lgbm = LGBMRegressor(**study.best_params)
# best_lgbm.fit(X_train, y_train)
# print("✅ Best LightGBM Parameters:", study.best_params)

# # 🔹 Predict & Save
# y_test_pred = best_lgbm.predict(X_test)
# submission = pd.DataFrame({"Id": test["Id"], "SalePrice": y_test_pred})
# submission.to_csv("LightGBM_Optimized.csv", index=False)
# print("✅ LightGBM predictions saved!")

[I 2025-03-09 11:51:53,421] A new study created in memory with name: no-name-47c41dc3-59bf-4f9b-8f36-40909de4c9e2


[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001728 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3560
[LightGBM] [Info] Number of data points in the train set: 1161, number of used features: 135
[LightGBM] [Info] Start training from score 180408.150732
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

[I 2025-03-09 11:51:56,350] Trial 0 finished with value: 0.9076940289317733 and parameters: {'n_estimators': 550, 'learning_rate': 0.08398374167117591, 'max_depth': 11, 'num_leaves': 191, 'subsample': 0.7839564507497112, 'colsample_bytree': 0.8768522215115062}. Best is trial 0 with value: 0.9076940289317733.


[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000909 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3560
[LightGBM] [Info] Number of data points in the train set: 1161, number of used features: 135
[LightGBM] [Info] Start training from score 180408.150732
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

[I 2025-03-09 11:52:00,217] Trial 1 finished with value: 0.9112327637085013 and parameters: {'n_estimators': 600, 'learning_rate': 0.019274666102196643, 'max_depth': 15, 'num_leaves': 99, 'subsample': 0.9842505672745221, 'colsample_bytree': 0.6710788217433087}. Best is trial 1 with value: 0.9112327637085013.


...

[I 2025-03-09 11:53:19,688] Trial 48 finished with value: 0.9130602039839933 and parameters: {'n_estimators': 150, 'learning_rate': 0.09359145084787804, 'max_depth': 4, 'num_leaves': 237, 'subsample': 0.9992337227400723, 'colsample_bytree': 0.7540934183918759}. Best is trial 42 with value: 0.9179524372979424.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2025-03-09 11:53:20,482] Trial 49 finished with value: 0.9117769534234368 and parameters: {'n_estimators': 100, 'learning_rate': 0.12774168467843527, 'max_depth': 9, 'num_leaves': 201, 'subsample': 0.9625783245223438, 'colsample_bytree': 0.6438836211127906}. Best is trial 42 with value: 0.9179524372979424.


[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001172 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3845
[LightGBM] [Info] Number of data points in the train set: 1452, number of used features: 143
[LightGBM] [Info] Start training from score 180372.070248
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

: 

In [ ]:
# from catboost import CatBoostRegressor

# # 🔹 Define Objective Function
# def objective(trial):
#     params = {
#         "iterations": trial.suggest_int("iterations", 500, 2000, step=100),
#         "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.2),
#         "depth": trial.suggest_int("depth", 4, 12),
#         "l2_leaf_reg": trial.suggest_float("l2_leaf_reg", 1, 10),
#         "random_state": 42,
#         "verbose": 0
#     }
#     model = CatBoostRegressor(**params)
#     score = cross_val_score(model, X_train, y_train, cv=5, scoring="r2").mean()
#     return score

# # 🔹 Run Optimization
# study = optuna.create_study(direction="maximize")
# study.optimize(objective, n_trials=50)

# # 🔹 Train Best Model
# best_cat = CatBoostRegressor(**study.best_params, verbose=200)
# best_cat.fit(X_train, y_train)
# print("✅ Best CatBoost Parameters:", study.best_params)

# # 🔹 Predict & Save
# y_test_pred = best_cat.predict(X_test)
# submission = pd.DataFrame({"Id": sample_submission["Id"], "SalePrice": y_test_pred})
# submission.to_csv("CatBoost_Optimized.csv", index=False)
# print("✅ CatBoost predictions saved!")